 # Capstone Project - The Battle of Neighborhoods

## Import Libraries

In this section we import the libraries that will be required to process the data.

The first library is Pandas.
Pandas is an open source, BSD-licensed library, providing high-performance, easy-to-use data structures and data analysis tools for the Python programming language.

In [1]:
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

#!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim
import urllib.request
import json
from bs4 import BeautifulSoup
from urllib.request import urlopen
import requests
from pandas.io.json import json_normalize

import matplotlib.cm as cm
import matplotlib.colors as colors
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.pyplot as plt
import matplotlib.colors as colors
%matplotlib inline
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes
import folium

print('Libraries imported.')

Libraries imported.


## Download and Explore Dataset


Download and Explore Dataset
Neighborhood has a total of 5 boroughs and 306 neighborhoods. In order to segement the neighborhoods and explore them, we will essentially need a dataset that contains the 5 boroughs and the neighborhoods that exist in each borough as well as the the latitude and logitude coordinates of each neighborhood.

Luckily, this dataset exists for free on the web. Feel free to try to find this dataset on your own, but here is the link to the dataset: https://geo.nyu.edu/catalog/nyu_2451_34572

I used the data placed on a server as in Week 3 exercise.

In [2]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

Data downloaded!


#### Tranform the data into a *pandas* dataframe

In [3]:
neighborhoods_data = newyork_data['features']
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [4]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

#### Use geopy library to get the latitude and longitude values of New York City.

In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent <em>ny_explorer</em>, as shown below.

In [5]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


#### Create a map of New York with neighborhoods superimposed on top.

In [6]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_data.head()

Borough        Neighborhood   Latitude  Longitude
0  Manhattan         Marble Hill  40.876551 -73.910660
1  Manhattan           Chinatown  40.715618 -73.994279
2  Manhattan  Washington Heights  40.851903 -73.936900
3  Manhattan              Inwood  40.867684 -73.921210
4  Manhattan    Hamilton Heights  40.823604 -73.949688

In [7]:
import folium
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(manhattan_data['Latitude'], manhattan_data['Longitude'], manhattan_data['Borough'], manhattan_data['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

## Foursquare venues


In [8]:
import urllib
def getNearbyVenues(names, latitudes, longitudes, radius=5000, categoryIds=''):
    try:
        venues_list=[]
        for name, lat, lng in zip(names, latitudes, longitudes):
            #print(name)

            # create the API request URL
            url = 'https://api.foursquare.com/v2/venues/search?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, VERSION, lat, lng, radius, LIMIT)

            if (categoryIds != ''):
                url = url + '&categoryId={}'
                url = url.format(categoryIds)

            # make the GET request
            response = requests.get(url).json()
            results = response["response"]['venues']

            # return only relevant information for each nearby venue
            for v in results:
                success = False
                try:
                    category = v['categories'][0]['name']
                    success = True
                except:
                    pass

                if success:
                    venues_list.append([(
                        name, 
                        lat, 
                        lng, 
                        v['name'], 
                        v['location']['lat'], 
                        v['location']['lng'],
                        v['categories'][0]['name']
                    )])

        nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
        nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude',  
                  'Venue Category']
    
    except:
        print(url)
        print(response)
        print(results)
        print(nearby_venues)

    return(nearby_venues)

In [9]:
LIMIT = 500 
radius = 5000 
CLIENT_ID = 'ZMHWBS0SR12Z3YDYVHJVTZPRK3U1ZP3I2TYQAJ5CU3JUHMB5'
CLIENT_SECRET = 'H3TT0XT3P5TIAFCV1Y2UUVLF42N44DICNKLUELK34H2TKLFR'
VERSION = '20181020'

In [10]:
#https://developer.foursquare.com/docs/resources/categories
#Indian Restaurant = 4bf58dd8d48988d10f941735
neighborhoods = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
newyork_venues_indian = getNearbyVenues(names=neighborhoods['Neighborhood'], latitudes=neighborhoods['Latitude'], longitudes=neighborhoods['Longitude'], radius=10000, categoryIds='4bf58dd8d48988d10f941735')
newyork_venues_indian

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0             Marble Hill              40.876551              -73.910660   
1             Marble Hill              40.876551              -73.910660   
2             Marble Hill              40.876551              -73.910660   
3             Marble Hill              40.876551              -73.910660   
4             Marble Hill              40.876551              -73.910660   
5             Marble Hill              40.876551              -73.910660   
6             Marble Hill              40.876551              -73.910660   
7             Marble Hill              40.876551              -73.910660   
8             Marble Hill              40.876551              -73.910660   
9             Marble Hill              40.876551              -73.910660   
10            Marble Hill              40.876551              -73.910660   
11            Marble Hill              40.876551              -73.910660   
12            Marble Hill              40.876551              -73.910660   
13            Marble Hill              40.876551              -73.910660   
14            Marble Hill              40.876551              -73.910660   
15            Marble Hill              40.876551              -73.910660   
16            Marble Hill              40.876551              -73.910660   
17            Marble Hill              40.876551              -73.910660   
18            Marble Hill              40.876551              -73.910660   
19            Marble Hill              40.876551              -73.910660   
20            Marble Hill              40.876551              -73.910660   
21            Marble Hill              40.876551              -73.910660   
22            Marble Hill              40.876551              -73.910660   
23            Marble Hill              40.876551              -73.910660   
24            Marble Hill              40.876551              -73.910660   
25            Marble Hill              40.876551              -73.910660   
26            Marble Hill              40.876551              -73.910660   
27            Marble Hill              40.876551              -73.910660   
28            Marble Hill              40.876551              -73.910660   
29            Marble Hill              40.876551              -73.910660   
30            Marble Hill              40.876551              -73.910660   
31            Marble Hill              40.876551              -73.910660   
32            Marble Hill              40.876551              -73.910660   
33            Marble Hill              40.876551              -73.910660   
34            Marble Hill              40.876551              -73.910660   
35            Marble Hill              40.876551              -73.910660   
36            Marble Hill              40.876551              -73.910660   
37            Marble Hill              40.876551              -73.910660   
38            Marble Hill              40.876551              -73.910660   
39            Marble Hill              40.876551              -73.910660   
40            Marble Hill              40.876551              -73.910660   
41            Marble Hill              40.876551              -73.910660   
42            Marble Hill              40.876551              -73.910660   
43            Marble Hill              40.876551              -73.910660   
44            Marble Hill              40.876551              -73.910660   
45            Marble Hill              40.876551              -73.910660   
46            Marble Hill              40.876551              -73.910660   
47              Chinatown              40.715618              -73.994279   
48              Chinatown              40.715618              -73.994279   
49              Chinatown              40.715618              -73.994279   
50              Chinatown              40.715618              -73.994279   
51              Chinatown              40.715618             

In [11]:
newyork_venues_indian.shape


(1997, 7)

In [12]:
def addToMap(df, color, existingMap):
    for lat, lng, local, venue, venueCat in zip(df['Venue Latitude'], df['Venue Longitude'], df['Neighborhood'], df['Venue'], df['Venue Category']):
        label = '{} ({}) - {}'.format(venue, venueCat, local)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color=color,
            fill=True,
            fill_color=color,
            fill_opacity=0.7).add_to(existingMap)

In [13]:
map_newyork_indian = folium.Map(location=[latitude, longitude], zoom_start=10)
addToMap(newyork_venues_indian, 'red', map_newyork_indian)

map_newyork_indian

In [14]:
def addColumn(startDf, columnTitle, dataDf):
    grouped = dataDf.groupby('Neighborhood').count()
    
    for n in startDf['Neighborhood']:
        try:
            startDf.loc[startDf['Neighborhood'] == n,columnTitle] = grouped.loc[n, 'Venue']
        except:
            startDf.loc[startDf['Neighborhood'] == n,columnTitle] = 0

In [30]:
manhattan_grouped = newyork_venues_indian.groupby('Neighborhood').count()
manhattan_grouped
print('There are {} uniques categories.'.format(len(newyork_venues_indian['Venue Category'].unique())))


There are 16 uniques categories.


## 3. Analyze Each Neighborhood

In [16]:
# one hot encoding
manhattan_onehot = pd.get_dummies(newyork_venues_indian[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
manhattan_onehot['Neighborhood'] = newyork_venues_indian['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [manhattan_onehot.columns[-1]] + list(manhattan_onehot.columns[:-1])
manhattan_onehot = manhattan_onehot[fixed_columns]

manhattan_onehot

Neighborhood  Asian Restaurant  Caribbean Restaurant  \
0             Marble Hill                 0                     0   
1             Marble Hill                 0                     0   
2             Marble Hill                 0                     0   
3             Marble Hill                 0                     0   
4             Marble Hill                 0                     0   
5             Marble Hill                 0                     0   
6             Marble Hill                 0                     0   
7             Marble Hill                 0                     0   
8             Marble Hill                 0                     0   
9             Marble Hill                 0                     0   
10            Marble Hill                 0                     0   
11            Marble Hill                 0                     0   
12            Marble Hill                 0                     0   
13            Marble Hill                 0                     0   
14            Marble Hill                 0                     0   
15            Marble Hill                 0                     0   
16            Marble Hill                 0                     0   
17            Marble Hill                 0                     0   
18            Marble Hill                 0                     0   
19            Marble Hill                 0                     0   
20            Marble Hill                 0                     0   
21            Marble Hill                 0                     0   
22            Marble Hill                 0                     0   
23            Marble Hill                 0                     0   
24            Marble Hill                 0                     0   
25            Marble Hill                 0                     1   
26            Marble Hill                 0                     0   
27            Marble Hill                 0                     0   
28            Marble Hill                 0                     0   
29            Marble Hill                 0                     0   
30            Marble Hill                 0                     0   
31            Marble Hill                 0                     0   
32            Marble Hill                 0                     0   
33            Marble Hill                 0                     0   
34            Marble Hill                 0                     0   
35            Marble Hill                 0                     0   
36            Marble Hill                 0                     0   
37            Marble Hill                 0                     0   
38            Marble Hill                 0                     0   
39            Marble Hill                 0                     0   
40            Marble Hill                 0                     0   
41            Marble Hill                 0                     0   
42            Marble Hill                 0                     0   
43            Marble Hill                 0                     0   
44            Marble Hill                 0                     0   
45            Marble Hill                 0                     0   
46            Marble Hill                 0                     0   
47              Chinatown                 0                     0   
48              Chinatown                 0                     0   
49              Chinatown                 0                     0   
50              Chinatown                 0                     0   
51              Chinatown                 0                     0   
52              Chinatown                 0                     0   
53              Chinatown                 0                     0   
54              Chinatown                 0                     0   
55              Chinatown                 0                     0   
56              Chinatown                 0                     0   
57         

In [17]:
manhattan_grouped = manhattan_onehot.groupby('Neighborhood').mean().reset_index()
manhattan_grouped

Neighborhood  Asian Restaurant  Caribbean Restaurant  \
0     Battery Park City              0.00              0.000000   
1         Carnegie Hill              0.00              0.000000   
2        Central Harlem              0.02              0.000000   
3               Chelsea              0.00              0.000000   
4             Chinatown              0.00              0.000000   
5          Civic Center              0.00              0.000000   
6               Clinton              0.00              0.000000   
7           East Harlem              0.00              0.000000   
8          East Village              0.00              0.000000   
9    Financial District              0.00              0.000000   
10             Flatiron              0.00              0.000000   
11             Gramercy              0.00              0.000000   
12    Greenwich Village              0.00              0.000000   
13     Hamilton Heights              0.02              0.000000   
14         Hudson Yards              0.00              0.000000   
15               Inwood              0.02              0.000000   
16           Lenox Hill              0.00              0.000000   
17       Lincoln Square              0.00              0.000000   
18         Little Italy              0.00              0.000000   
19      Lower East Side              0.00              0.000000   
20     Manhattan Valley              0.00              0.000000   
21       Manhattanville              0.02              0.000000   
22          Marble Hill              0.00              0.021277   
23              Midtown              0.00              0.000000   
24        Midtown South              0.00              0.000000   
25  Morningside Heights              0.00              0.000000   
26          Murray Hill              0.00              0.000000   
27                 Noho              0.00              0.000000   
28     Roosevelt Island              0.00              0.000000   
29                 Soho              0.00              0.000000   
30      Stuyvesant Town              0.00              0.000000   
31         Sutton Place              0.00              0.000000   
32              Tribeca              0.00              0.000000   
33           Tudor City              0.00              0.000000   
34           Turtle Bay              0.00              0.000000   
35      Upper East Side              0.00              0.000000   
36      Upper West Side              0.00              0.000000   
37   Washington Heights              0.02              0.000000   
38         West Village              0.00              0.000000   
39            Yorkville              0.00              0.000000   

    Chinese Restaurant  Deli / Bodega  Diner  Financial or Legal Service  \
0                 0.02           0.02   0.00                        0.00   
1                 0.02           0.02   0.00                        0.00   
2                 0.00           0.02   0.02                        0.00   
3                 0.02           0.02   0.00                        0.00   
4                 0.02           0.02   0.00                        0.00   
5                 0.02           0.02   0.00                        0.00   
6                 0.02           0.02   0.00                        0.00   
7                 0.02           0.02   0.00                        0.00   
8                 0.02           0.02   0.00                        0.00   
9                 0.02           0.02   0.00                        0.00   
10                0.02           0.02   0.00                        0.00   
11                0.02           0.02   0.00                        0.00   
12                0.02           0.02   0.00                        0.00   
13                0.00           0.02   0.02                        0.02   
14                0.02           0.02   0.00                        0.00   
15                0.00           0.00   0.00   

In [18]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [19]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = manhattan_grouped['Neighborhood']

for ind in np.arange(manhattan_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(manhattan_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

Neighborhood 1st Most Common Venue    2nd Most Common Venue  \
0     Battery Park City     Indian Restaurant  South Indian Restaurant   
1         Carnegie Hill     Indian Restaurant  South Indian Restaurant   
2        Central Harlem     Indian Restaurant  South Indian Restaurant   
3               Chelsea     Indian Restaurant  South Indian Restaurant   
4             Chinatown     Indian Restaurant  South Indian Restaurant   
5          Civic Center     Indian Restaurant  South Indian Restaurant   
6               Clinton     Indian Restaurant  South Indian Restaurant   
7           East Harlem     Indian Restaurant  South Indian Restaurant   
8          East Village     Indian Restaurant  South Indian Restaurant   
9    Financial District     Indian Restaurant  South Indian Restaurant   
10             Flatiron     Indian Restaurant  South Indian Restaurant   
11             Gramercy     Indian Restaurant  South Indian Restaurant   
12    Greenwich Village     Indian Restaurant  South Indian Restaurant   
13     Hamilton Heights     Indian Restaurant  South Indian Restaurant   
14         Hudson Yards     Indian Restaurant  South Indian Restaurant   
15               Inwood     Indian Restaurant       Tibetan Restaurant   
16           Lenox Hill     Indian Restaurant  South Indian Restaurant   
17       Lincoln Square     Indian Restaurant  South Indian Restaurant   
18         Little Italy     Indian Restaurant  South Indian Restaurant   
19      Lower East Side     Indian Restaurant  South Indian Restaurant   
20     Manhattan Valley     Indian Restaurant  South Indian Restaurant   
21       Manhattanville     Indian Restaurant  South Indian Restaurant   
22          Marble Hill     Indian Restaurant  South Indian Restaurant   
23              Midtown     Indian Restaurant  South Indian Restaurant   
24        Midtown South     Indian Restaurant  South Indian Restaurant   
25  Morningside Heights     Indian Restaurant  South Indian Restaurant   
26          Murray Hill     Indian Restaurant  South Indian Restaurant   
27                 Noho     Indian Restaurant  South Indian Restaurant   
28     Roosevelt Island     Indian Restaurant  South Indian Restaurant   
29                 Soho     Indian Restaurant  South Indian Restaurant   
30      Stuyvesant Town     Indian Restaurant  South Indian Restaurant   
31         Sutton Place     Indian Restaurant  South Indian Restaurant   
32              Tribeca     Indian Restaurant  South Indian Restaurant   
33           Tudor City     Indian Restaurant  South Indian Restaurant   
34           Turtle Bay     Indian Restaurant  South Indian Restaurant   
35      Upper East Side     Indian Restaurant  South Indian Restaurant   
36      Upper West Side     Indian Restaurant  South Indian Restaurant   
37   Washington Heights     Indian Restaurant       Tibetan Restaurant   
38         West Village     Indian Restaurant  South Indian Restaurant   
39            Yorkville     Indian Restaurant  South Indian Restaurant   

            3rd Most Common Venue    4th Most Common Venue  \
0   Vegetarian / Vegan Restaurant       Tibetan Restaurant   
1   Vegetarian / Vegan Restaurant       Tibetan Restaurant   
2   Vegetarian / Vegan Restaurant       Tibetan Restaurant   
3   Vegetarian / Vegan Restaurant       Tibetan Restaurant   
4   Vegetarian / Vegan Restaurant       Tibetan Restaurant   
5   Vegetarian / Vegan Restaurant       Tibetan Restaurant   
6   Vegetarian / Vegan Restaurant       Tibetan Restaurant   
7   Vegetarian / Vegan Restaurant       Tibetan Restaurant   
8   Vegetarian / Vegan Restaurant       Tibetan Restaurant   
9   Vegetarian / Vegan Restaurant       Tibetan Restaurant   
10  Vegetarian / Vegan Restaurant       Tibetan Restaurant   
11  Vegetarian / Vegan Restaurant       Tibetan Restaurant   
12  Vegetarian / Vegan Restaurant       Tibetan Restaurant   
13  Vegetarian / Vegan Restaurant       Tibetan Restaurant   
14  Vegetarian / Vegan Restaurant       Tibeta

Cluster Neighborhoods


In [20]:
# set number of clusters
kclusters = 5

manhattan_grouped_clustering = manhattan_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 1, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [21]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

manhattan_merged = manhattan_data
manhattan_merged = manhattan_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

manhattan_merged

Borough         Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Manhattan          Marble Hill  40.876551 -73.910660               3   
1   Manhattan            Chinatown  40.715618 -73.994279               0   
2   Manhattan   Washington Heights  40.851903 -73.936900               2   
3   Manhattan               Inwood  40.867684 -73.921210               2   
4   Manhattan     Hamilton Heights  40.823604 -73.949688               1   
5   Manhattan       Manhattanville  40.816934 -73.957385               1   
6   Manhattan       Central Harlem  40.815976 -73.943211               1   
7   Manhattan          East Harlem  40.792249 -73.944182               0   
8   Manhattan      Upper East Side  40.775639 -73.960508               0   
9   Manhattan            Yorkville  40.775930 -73.947118               0   
10  Manhattan           Lenox Hill  40.768113 -73.958860               0   
11  Manhattan     Roosevelt Island  40.762160 -73.949168               0   
12  Manhattan      Upper West Side  40.787658 -73.977059               4   
13  Manhattan       Lincoln Square  40.773529 -73.985338               4   
14  Manhattan              Clinton  40.759101 -73.996119               0   
15  Manhattan              Midtown  40.754691 -73.981669               0   
16  Manhattan          Murray Hill  40.748303 -73.978332               0   
17  Manhattan              Chelsea  40.744035 -74.003116               0   
18  Manhattan    Greenwich Village  40.726933 -73.999914               0   
19  Manhattan         East Village  40.727847 -73.982226               0   
20  Manhattan      Lower East Side  40.717807 -73.980890               0   
21  Manhattan              Tribeca  40.721522 -74.010683               0   
22  Manhattan         Little Italy  40.719324 -73.997305               0   
23  Manhattan                 Soho  40.722184 -74.000657               0   
24  Manhattan         West Village  40.734434 -74.006180               0   
25  Manhattan     Manhattan Valley  40.797307 -73.964286               4   
26  Manhattan  Morningside Heights  40.808000 -73.963896               4   
27  Manhattan             Gramercy  40.737210 -73.981376               0   
28  Manhattan    Battery Park City  40.711932 -74.016869               0   
29  Manhattan   Financial District  40.707107 -74.010665               0   
30  Manhattan        Carnegie Hill  40.782683 -73.953256               0   
31  Manhattan                 Noho  40.723259 -73.988434               0   
32  Manhattan         Civic Center  40.715229 -74.005415               0   
33  Manhattan        Midtown South  40.748510 -73.988713               0   
34  Manhattan         Sutton Place  40.760280 -73.963556               0   
35  Manhattan           Turtle Bay  40.752042 -73.967708               0   
36  Manhattan           Tudor City  40.746917 -73.971219               0   
37  Manhattan      Stuyvesant Town  40.731000 -73.974052               0   
38  Manhattan             Flatiron  40.739673 -73.990947               0   
39  Manhattan         Hudson Yards  40.756658 -74.000111               0   

   1st Most Common Venue    2nd Most Common Venue  \
0      Indian Restaurant  South Indian Restaurant   
1      Indian Restaurant  South Indian Restaurant   
2      Indian Restaurant       Tibetan Restaurant   
3      Indian Restaurant       Tibetan Restaurant   
4      Indian Restaurant  South Indian Restaurant   
5      Indian Restaurant  South Indian Restaurant   
6      Indian Restaurant  South Indian Restaurant   
7      Indian Restaurant  South Indian Restaurant   
8      Indian Restaurant  South Indian Restaurant   
9      Indian Restaurant  South Indian Restaurant   
10     Indian Restaurant  South Indian Restaurant   
11     Indian Restaurant  South Indian Restaurant   
12     Indian Restaurant  South Indian Restaurant   
13     Indian Restaurant  South Indian Restaurant   
14     Indian Restaurant  South Indian Restaurant   
15     Indian Restaurant  South Indian Re

In [22]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(manhattan_merged['Latitude'], manhattan_merged['Longitude'], manhattan_merged['Neighborhood'], manhattan_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [23]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 0, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue    2nd Most Common Venue  \
1            Chinatown     Indian Restaurant  South Indian Restaurant   
7          East Harlem     Indian Restaurant  South Indian Restaurant   
8      Upper East Side     Indian Restaurant  South Indian Restaurant   
9            Yorkville     Indian Restaurant  South Indian Restaurant   
10          Lenox Hill     Indian Restaurant  South Indian Restaurant   
11    Roosevelt Island     Indian Restaurant  South Indian Restaurant   
14             Clinton     Indian Restaurant  South Indian Restaurant   
15             Midtown     Indian Restaurant  South Indian Restaurant   
16         Murray Hill     Indian Restaurant  South Indian Restaurant   
17             Chelsea     Indian Restaurant  South Indian Restaurant   
18   Greenwich Village     Indian Restaurant  South Indian Restaurant   
19        East Village     Indian Restaurant  South Indian Restaurant   
20     Lower East Side     Indian Restaurant  South Indian Restaurant   
21             Tribeca     Indian Restaurant  South Indian Restaurant   
22        Little Italy     Indian Restaurant  South Indian Restaurant   
23                Soho     Indian Restaurant  South Indian Restaurant   
24        West Village     Indian Restaurant  South Indian Restaurant   
27            Gramercy     Indian Restaurant  South Indian Restaurant   
28   Battery Park City     Indian Restaurant  South Indian Restaurant   
29  Financial District     Indian Restaurant  South Indian Restaurant   
30       Carnegie Hill     Indian Restaurant  South Indian Restaurant   
31                Noho     Indian Restaurant  South Indian Restaurant   
32        Civic Center     Indian Restaurant  South Indian Restaurant   
33       Midtown South     Indian Restaurant  South Indian Restaurant   
34        Sutton Place     Indian Restaurant  South Indian Restaurant   
35          Turtle Bay     Indian Restaurant  South Indian Restaurant   
36          Tudor City     Indian Restaurant  South Indian Restaurant   
37     Stuyvesant Town     Indian Restaurant  South Indian Restaurant   
38            Flatiron     Indian Restaurant  South Indian Restaurant   
39        Hudson Yards     Indian Restaurant  South Indian Restaurant   

            3rd Most Common Venue 4th Most Common Venue  \
1   Vegetarian / Vegan Restaurant    Tibetan Restaurant   
7   Vegetarian / Vegan Restaurant    Tibetan Restaurant   
8   Vegetarian / Vegan Restaurant    Tibetan Restaurant   
9   Vegetarian / Vegan Restaurant    Tibetan Restaurant   
10  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
11  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
14  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
15  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
16  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
17  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
18  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
19  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
20  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
21  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
22  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
23  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
24  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
27  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
28  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
29  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
30  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
31  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
32  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
33  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
34  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
35  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
36  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
37  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
38  Vegetarian / Vegan Restaurant  

In [24]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 1, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]


Neighborhood 1st Most Common Venue    2nd Most Common Venue  \
4  Hamilton Heights     Indian Restaurant  South Indian Restaurant   
5    Manhattanville     Indian Restaurant  South Indian Restaurant   
6    Central Harlem     Indian Restaurant  South Indian Restaurant   

           3rd Most Common Venue 4th Most Common Venue  \
4  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
5  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
6  Vegetarian / Vegan Restaurant    Tibetan Restaurant   

     5th Most Common Venue 6th Most Common Venue       7th Most Common Venue  \
4  North Indian Restaurant    Italian Restaurant  Financial or Legal Service   
5  North Indian Restaurant    Italian Restaurant  Financial or Legal Service   
6  North Indian Restaurant    Italian Restaurant                       Diner   

  8th Most Common Venue 9th Most Common Venue     10th Most Common Venue  
4                 Diner         Deli / Bodega           Asian Restaurant  
5                 Diner         Deli / Bodega           Asian Restaurant  
6         Deli / Bodega      Asian Restaurant  Indian Chinese Restaurant

In [25]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 2, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
2  Washington Heights     Indian Restaurant    Tibetan Restaurant   
3              Inwood     Indian Restaurant    Tibetan Restaurant   

     3rd Most Common Venue    4th Most Common Venue 5th Most Common Venue  \
2  South Indian Restaurant  North Indian Restaurant    Italian Restaurant   
3  South Indian Restaurant  North Indian Restaurant    Italian Restaurant   

  6th Most Common Venue 7th Most Common Venue       8th Most Common Venue  \
2  Himalayan Restaurant      Halal Restaurant  Financial or Legal Service   
3  Himalayan Restaurant      Halal Restaurant                  Food Truck   

        9th Most Common Venue         10th Most Common Venue  
2            Asian Restaurant  Vegetarian / Vegan Restaurant  
3  Financial or Legal Service               Asian Restaurant

In [26]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 3, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]


Neighborhood 1st Most Common Venue    2nd Most Common Venue  \
0  Marble Hill     Indian Restaurant  South Indian Restaurant   

       3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0  Indian Chinese Restaurant  Himalayan Restaurant  Caribbean Restaurant   

           6th Most Common Venue 7th Most Common Venue  \
0  Vegetarian / Vegan Restaurant    Tibetan Restaurant   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0  North Indian Restaurant    Italian Restaurant       Halal Restaurant

In [27]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 4, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]


Neighborhood 1st Most Common Venue    2nd Most Common Venue  \
12      Upper West Side     Indian Restaurant  South Indian Restaurant   
13       Lincoln Square     Indian Restaurant  South Indian Restaurant   
25     Manhattan Valley     Indian Restaurant  South Indian Restaurant   
26  Morningside Heights     Indian Restaurant  South Indian Restaurant   

            3rd Most Common Venue 4th Most Common Venue  \
12  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
13  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
25  Vegetarian / Vegan Restaurant    Tibetan Restaurant   
26  Vegetarian / Vegan Restaurant    Tibetan Restaurant   

      5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
12  North Indian Restaurant    Italian Restaurant                 Diner   
13  North Indian Restaurant    Italian Restaurant         Deli / Bodega   
25  North Indian Restaurant    Italian Restaurant         Deli / Bodega   
26  North Indian Restaurant    Italian Restaurant                 Diner   

   8th Most Common Venue      9th Most Common Venue 10th Most Common Venue  
12         Deli / Bodega  Indian Chinese Restaurant   Himalayan Restaurant  
13    Chinese Restaurant  Indian Chinese Restaurant   Himalayan Restaurant  
25    Chinese Restaurant  Indian Chinese Restaurant   Himalayan Restaurant  
26         Deli / Bodega  Indian Chinese Restaurant   Himalayan Restaurant